In [6]:
import pandas as pd
from pathlib import Path


### Load all json

In [8]:
from pathlib import Path
path_all_json = Path("json_files")
path_all_json.exists()

True

In [9]:
import json
all_json_path = list(path_all_json.glob("*/*.json"))
len(all_json_path)

28224

In [11]:
def nested_lookup(obj, keys, default='NA'):
	current = obj
	for key in keys:
		current = current if isinstance(current, list) else [current]
		try:
			current = next(sub[key] for sub in current if key in sub)
		except StopIteration:
			return default
	return current

In [22]:
def open_and_get_dataframe(path: Path):
	with open(path, "r") as f:
		json_example : dict = json.load(f)
	if "similar" not in json_example:
		return pd.DataFrame(columns=["original_card","sanitized"])
	df_ret = pd.DataFrame(json_example["similar"],columns=["sanitized"])
	df_ret["original_card"] = nested_lookup(json_example, ("container","json_dict","card","sanitized"))

	# allign column
	return df_ret
df = open_and_get_dataframe(all_json_path[0])
# Pïvot the dataframe to get all sanitized card in columns
df

sanitized     original_card
0         oppression  painful-quandary
1  underworld-dreams  painful-quandary
2    lilianas-caress  painful-quandary
3          waste-not  painful-quandary
4             megrim  painful-quandary
5     necrogen-mists  painful-quandary

In [13]:
df.columns

Index(['sanitized', 'salt', 'original_card'], dtype='object')

In [14]:
from tqdm.notebook import tqdm
def open_and_get_dataframe_pbar(path: Path, pbar: tqdm):
	pbar.set_description(str(path))

	ret = open_and_get_dataframe(path)
	pbar.update()
	return ret
with tqdm(total=len(all_json_path)) as pbar:
	df_all = pd.concat([open_and_get_dataframe_pbar(path, pbar) for path in all_json_path]).rename(columns={"sanitized":"similar_cards"})


  0%|          | 0/28224 [00:00<?, ?it/s]

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)

IOPub message rate exceeded.
The Jupyter serve

In [24]:
df_all = df_all.drop_duplicates()
df_all

similar_cards     original_card
0             oppression  painful-quandary
1      underworld-dreams  painful-quandary
2        lilianas-caress  painful-quandary
3              waste-not  painful-quandary
4                 megrim  painful-quandary
..                   ...               ...
1   sandwurm-convergence     ramunap-hydra
2         carnage-tyrant     ramunap-hydra
3   ghalta-primal-hunger     ramunap-hydra
4          gigantosaurus     ramunap-hydra
5     aggressive-mammoth     ramunap-hydra

[168781 rows x 2 columns]

In [16]:
pd.DataFrame(df_all.groupby("original_card").size().rename("size"))#.query("size != 6")

size
original_card                     
_____-_____-_____-trespasser     6
_____-_____-rocketship           6
_____-balls-of-fire              6
_____-bird-gets-the-worm         6
_____-goblin                     6
...                            ...
zurgo-bellstriker                6
zurgo-helmsmasher                6
zurs-weirding                    6
zurzoth-chaos-rider              6
zygon-infiltrator                6

[28167 rows x 1 columns]

In [17]:
pd.DataFrame(df_all.groupby("similar_cards").size().rename("size"))#.query("size != 6")

size
similar_cards              
abandoned-sarcophagus     2
abbot-of-keral-keep      28
abeyance                  8
abhorrent-overlord       10
abnormal-endurance       17
...                     ...
zuran-orb                 7
zuran-spellcaster        16
zurgo-bellstriker        43
zurgo-helmsmasher        13
zurs-weirding             4

[12488 rows x 1 columns]

In [36]:
df_all.query("original_card == 'sakashima-the-impostor'")

similar_cards           original_card
0                 clone  sakashima-the-impostor
1   phyrexian-metamorph  sakashima-the-impostor
2   clever-impersonator  sakashima-the-impostor
3      progenitor-mimic  sakashima-the-impostor
4          stunt-double  sakashima-the-impostor
5  vizier-of-many-faces  sakashima-the-impostor

In [40]:
import networkx as nx
# Create a graph from the datafram with source->Destination column
G = nx.from_pandas_edgelist(df_all, source="original_card", target="similar_cards",create_using=nx.DiGraph)
G


In [41]:
G.edges

OutEdgeView([('painful-quandary', 'oppression'), ('painful-quandary', 'underworld-dreams'), ('painful-quandary', 'lilianas-caress'), ('painful-quandary', 'waste-not'), ('painful-quandary', 'megrim'), ('painful-quandary', 'necrogen-mists'), ('oppression', 'painful-quandary'), ('oppression', 'necrogen-mists'), ('oppression', 'bottomless-pit'), ('oppression', 'gibbering-descent'), ('oppression', 'words-of-waste'), ('oppression', 'lilianas-caress'), ('underworld-dreams', 'fate-unraveler'), ('underworld-dreams', 'kederekt-parasite'), ('underworld-dreams', 'nekusar-the-mindrazer'), ('underworld-dreams', 'psychosis-crawler'), ('underworld-dreams', 'spiteful-visions'), ('underworld-dreams', 'ob-nixilis-the-hate-twisted'), ('lilianas-caress', 'megrim'), ('lilianas-caress', 'raiders-wake'), ('lilianas-caress', 'waste-not'), ('lilianas-caress', 'lilianas-specter'), ('lilianas-caress', 'necrogen-mists'), ('lilianas-caress', 'cunning-lethemancer'), ('waste-not', 'lilianas-caress'), ('waste-not', 'm

In [42]:
louvain_community = nx.community.louvain_communities(G,seed=42)

louvain_community

[{'abandoned-campground',
  'abandoned-outpost',
  'abraded-bluffs',
  'abstergo-entertainment',
  'academy-ruins',
  'adarkar-sentinel',
  'adarkar-unicorn',
  'adarkar-wastes',
  'adventurers-guildhouse',
  'aether-hub',
  'afiya-grove',
  'akoum-refuge',
  'ally-encampment',
  'alpine-meadow',
  'an-havva-township',
  'ancient-amphitheater',
  'ancient-den',
  'ancient-spring',
  'ancient-tomb',
  'ancient-ziggurat',
  'animal-sanctuary',
  'arcane-sanctum',
  'arch-of-orazca',
  'archaeological-dig',
  'archaeomender',
  'archway-commons',
  'archway-of-innovation',
  'arctic-flats',
  'arctic-treeline',
  'arena-of-glory',
  'argoth-sanctum-of-nature',
  'arid-archway',
  'arid-mesa',
  'ark-of-blight',
  'ash-barrens',
  'aunties-hovel',
  'axgard-armory',
  'aysen-abbey',
  'azorius-chancery',
  'azorius-guildgate',
  'bad-river',
  'badlands',
  'baldurs-gate',
  'balduvian-trading-post',
  'ballroom',
  'bant-panorama',
  'barad-dur',
  'barbarian-ring',
  'barkchannel-pathway

In [43]:
len(community)

187

In [44]:
# Assign to each node its own community

node_community_mapping = {}
for i, community in enumerate(louvain_community):
    for node in community:
        node_community_mapping[node] = i
nx.set_node_attributes(G, node_community_mapping, 'community')

In [93]:
pd.concat([list(G.nodes.values()), list(G.nodes.values())],axis=0)

TypeError: cannot concatenate object of type '<class 'list'>'; only Series and DataFrame objs are valid

In [94]:
list(G.nodes.values())

[{'community': 25},
 {'community': 25},
 {'community': 4},
 {'community': 25},
 {'community': 25},
 {'community': 25},
 {'community': 25},
 {'community': 36},
 {'community': 36},
 {'community': 36},
 {'community': 36},
 {'community': 36},
 {'community': 36},
 {'community': 36},
 {'community': 28},
 {'community': 28},
 {'community': 28},
 {'community': 28},
 {'community': 28},
 {'community': 28},
 {'community': 28},
 {'community': 3},
 {'community': 28},
 {'community': 28},
 {'community': 28},
 {'community': 28},
 {'community': 28},
 {'community': 28},
 {'community': 21},
 {'community': 21},
 {'community': 21},
 {'community': 21},
 {'community': 21},
 {'community': 21},
 {'community': 21},
 {'community': 6},
 {'community': 6},
 {'community': 6},
 {'community': 6},
 {'community': 6},
 {'community': 6},
 {'community': 6},
 {'community': 41},
 {'community': 41},
 {'community': 41},
 {'community': 41},
 {'community': 41},
 {'community': 41},
 {'community': 41},
 {'community': 2},
 {'communi

In [47]:
nx.write_gml(G,"graph_v1.gml")

In [51]:
G["giant-growth"].

AtlasView({'vines-of-vastwood': {}, 'might-of-old-krosa': {}, 'groundswell': {}, 'blossoming-defense': {}, 'rangers-guile': {}, 'mutagenic-growth': {}})

In [78]:
df_comu_giant_growth = pd.DataFrame([(x,G.nodes[x]["community"]) for x in nx.all_neighbors(G,"giant-growth")],columns=["names","community"])
df_comu_giant_growth

names  community
0               bulk-up         22
1     moment-of-triumph         22
2               enlarge         22
3         bounding-wolf         12
4        impending-doom         22
..                  ...        ...
336  might-of-old-krosa         22
337         groundswell         22
338  blossoming-defense         22
339       rangers-guile         22
340    mutagenic-growth         22

[341 rows x 2 columns]

In [82]:
df_comu_giant_growth.groupby("community").agg(
	size=("names","size"),
	names_head=("names","first")
)


size          names_head
community                          
2             1  collision-colossus
4             1        hornet-cobra
5             3           chub-toad
9             2       ghitu-war-cry
10            4        scent-of-ivy
12           23       bounding-wolf
13            2  stormkeld-vanguard
14            4      akki-war-paint
17            1     heartwood-giant
21            1    culvert-ambusher
22          281             bulk-up
23            2   lurking-crocodile
24            1         flesh-blood
29            1     glissas-courier
31            3  unearthly-blizzard
33            5         mires-grasp
35            1        giant-badger
36            3      hunters-talent
38            1    applied-biomancy
39            1            go-forth